In [2]:
library(pscl)
library(MASS)
library(dplyr)
library(car)
library(corrplot)
df <- read.csv("clean_data.csv")


corrplot 0.95 loaded



In [3]:
numeric_vars <- df %>%
  select(where(is.numeric))

summary_stats <- numeric_vars %>%
  summarise(across(everything(),
                   list(Mean = ~mean(., na.rm = TRUE),
                        Median = ~median(., na.rm = TRUE),
                        SD = ~sd(., na.rm = TRUE),
                        Min = ~min(., na.rm = TRUE),
                        Max = ~max(., na.rm = TRUE)),
                   .names = "{.col}_{.fn}"))

summary_stats_t <- t(summary_stats)
print(summary_stats_t)

                                     [,1]
Number_of_Flights_Mean       2.435639e+01
Number_of_Flights_Median     5.000000e+00
Number_of_Flights_SD         6.742273e+01
Number_of_Flights_Min        1.000000e+00
Number_of_Flights_Max        1.226000e+03
Served_Population_Mean       9.937426e+05
Served_Population_Median     2.699935e+05
Served_Population_SD         2.479144e+06
Served_Population_Min        2.300000e+01
Served_Population_Max        3.372453e+07
Number_of_Events_Mean        9.763500e+01
Number_of_Events_Median      1.700000e+01
Number_of_Events_SD          2.590523e+02
Number_of_Events_Min         0.000000e+00
Number_of_Events_Max         6.079000e+03
GDP_per_capita_Mean          2.690592e+04
GDP_per_capita_Median        1.144770e+04
GDP_per_capita_SD            2.487818e+04
GDP_per_capita_Min           2.102365e+02
GDP_per_capita_Max           1.127264e+05
Land_area_Mean               4.148564e+06
Land_area_Median             1.557258e+06
Land_area_SD                 4.617

In [4]:
vif_model <- lm(numeric_vars[[1]] ~ ., data = numeric_vars[, -1])
vif_values <- vif(vif_model)
print(vif_values)

    Served_Population      Number_of_Events        GDP_per_capita 
             1.424350              1.430105              4.591687 
            Land_area          Unemployment Freedom_of_Expression 
             1.574135              1.270525             14.585125 
  Civil_Society_Index                   HDI       Life_Expectancy 
            13.931561             30.454321              9.553996 
 Mean_Schooling_Years 
            11.736238 


In [6]:
numeric_complete <- na.omit(numeric_vars)
cor_matrix <- cor(numeric_complete)
print(cor_matrix)

                      Number_of_Flights Served_Population Number_of_Events
Number_of_Flights           1.000000000       0.671699241      0.367851267
Served_Population           0.671699241       1.000000000      0.506996810
Number_of_Events            0.367851267       0.506996810      1.000000000
GDP_per_capita              0.083266657      -0.107883557     -0.097270848
Land_area                   0.007304305      -0.009571527     -0.159943385
Unemployment               -0.039639363      -0.026894147      0.077944485
Freedom_of_Expression      -0.013162926      -0.154830547      0.021788094
Civil_Society_Index        -0.015615442      -0.153716921      0.004262525
HDI                         0.102218228      -0.075387890     -0.098668654
Life_Expectancy             0.111275449      -0.035340725     -0.048171784
Mean_Schooling_Years        0.067418917      -0.112865885     -0.111281573
                      GDP_per_capita    Land_area Unemployment
Number_of_Flights         0.08326666 

In [17]:
df_model <- na.omit(df[, c("Number_of_Events", "Number_of_Flights", "HDI",
                           "Served_Population", "Land_area", 
                           "Unemployment", "Freedom_of_Expression")])

nb_model <- glm.nb(Number_of_Events ~ ., data = df_model, control = glm.control(maxit = 100))

summary(nb_model)


Call:
glm.nb(formula = Number_of_Events ~ ., data = df_model, control = glm.control(maxit = 100), 
    init.theta = 0.4173593549, link = log)

Coefficients:
                        Estimate Std. Error z value Pr(>|z|)    
(Intercept)            5.271e+00  2.296e-01  22.952  < 2e-16 ***
Number_of_Flights      4.101e-03  6.156e-04   6.661 2.72e-11 ***
HDI                   -2.751e+00  3.066e-01  -8.973  < 2e-16 ***
Served_Population      3.587e-07  1.679e-08  21.357  < 2e-16 ***
Land_area             -1.192e-07  7.361e-09 -16.190  < 2e-16 ***
Unemployment           4.779e-02  7.225e-03   6.616 3.70e-11 ***
Freedom_of_Expression  1.136e+00  1.185e-01   9.592  < 2e-16 ***
---
Signif. codes:  0 ‘***’ 0.001 ‘**’ 0.01 ‘*’ 0.05 ‘.’ 0.1 ‘ ’ 1

(Dispersion parameter for Negative Binomial(0.4174) family taken to be 1)

    Null deviance: 4369.5  on 2619  degrees of freedom
Residual deviance: 3164.7  on 2613  degrees of freedom
AIC: 25106

Number of Fisher Scoring iterations: 1


              Th

In [18]:
pR2(nb_model)

fitting null model for pseudo-r2


llh       llhNull            G2      McFadden          r2ML 
-1.254513e+04 -1.305647e+04  1.022676e+03  3.916357e-02  3.231694e-01 
         r2CU 
 3.231846e-01